In [ ]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import math
import scipy

from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

## Read in Measurements

In [ ]:
two_k_sampling_trafo = pd.read_csv(r'2000OhmSamplingTrafoSupply.csv')
one_k_sampling_trafo = pd.read_csv(r'1000OhmSamplingTrafoSupply.csv')
temperature_measurement = pd.read_csv(r'TempSamplingTrafoSupply.csv')
constant_sampling = pd.read_csv(r'1000OhmSampling.csv')
shielded_df = pd.read_csv(r'ContactPT1000HeatgunCooldown.csv')

# Calculation Function for $\vartheta(R_{PT1000})$
$\vartheta(R_{PT1000}) = \frac{-\alpha R_0 + \sqrt{\alpha^2R_0^2 - 4\beta R_0 \left(R_0 - R_{PT1000}\right)}}{2\beta R_0}$

with
* $\alpha = 3.9083 \cdot 10^{-3}$
* $\beta = -5.7750 \cdot 10^{-7}$
* $R_0 = 1000~\Omega$

In [ ]:
R_zero = 1000.0
A = 3.9083E-3
B = -5.7750E-7

def calc_temp(resistance):
    temp = (-R_zero * A + np.sqrt(R_zero*R_zero * A * A - 4* R_zero * B * (R_zero - resistance)))/(2*R_zero*B)
    return temp

In [ ]:
def plot_histogram(ax, data, bin_count, title, signal_name):
    n, bins, patches = ax.hist(data, bin_count, density=1, color='navy')
    mu = np.mean(data)
    sigma = np.std(data)
    y = ((1 / (np.sqrt(2 * np.pi) * sigma)) * np.exp(-0.5 * (1 / sigma * (bins - mu))**2))
    ax.plot(bins, y, color='darkorange')
    ax.set_title(title)
    ax.set_ylabel(signal_name + ' probability (normalized)')
    ax.set_xlabel(signal_name)
    # Plot sigma and mu lines
    ax.axvline(x=mu-sigma, ls='--', color='magenta')
    ax.axvline(x=mu+sigma, ls='--', color='magenta')
    ax.axvline(x=mu, ls='--', color='lawngreen')

    #Plot textbox
    textstr = '\n'.join((
        r'$\mu=%.2f$' % (mu, ),
        r'$\sigma=%.4f$' % (sigma, ),
        r'$N_{Sa} =%d$' % (len(data), )))
    props = dict(boxstyle='round', facecolor='wheat', alpha=0.5)
    ax.text(0.05, 0.95, textstr, transform=ax.transAxes, fontsize=14,
    verticalalignment='top', bbox=props)


--------------------
# Calculate Temperature from Resistance Value

In [ ]:
def calculate_temp_for_df(data_frame, resistance_col_name='ext_lf_corr', temp_col_name='temp_calculated'):
    data_frame[temp_col_name] = data_frame.apply(lambda row: calc_temp(row[resistance_col_name]) , axis=1)

In [ ]:
df_list = [one_k_sampling_trafo, two_k_sampling_trafo, temperature_measurement, constant_sampling, shielded_df]
for df in df_list:
    calculate_temp_for_df(df)


# Histograms  (Uncalibrated)

In [ ]:
plot_data = [(one_k_sampling_trafo, '1 kOhm Sampling Transformer powered', 0), (two_k_sampling_trafo, '2 kOhm Sampling Transformer powered' , 0), (constant_sampling, '1 kOhm Sampling', 100)]
signal_list = [('ext_lf_corr', 20), ('temp_calculated', 20)]

fig, axes = plt.subplots(nrows=len(plot_data), ncols=len(signal_list), figsize=(28,20))

for (data_df, title, start_idx), ax_rows in zip(plot_data, axes):
    for ax,sig in zip(ax_rows, signal_list):
        plot_histogram(ax, data_df[sig[0]][start_idx:], sig[1], title,sig[0])

        
plt.tight_layout()
plt.show()

# Startup of Moving Average Filter with $\alpha' = 0.005$

Filter difference equation: $y[n] = (1-\alpha')y[n-1] + \alpha'x[n]$

In [ ]:
fig, ax = plt.subplots(nrows=2, ncols=1, figsize=(28,6), sharex=True)
data = constant_sampling['ext_lf_corr'][:20]
ax[0].plot(constant_sampling['Time'][:20], data)
ax[1].plot(constant_sampling['Time'][:20], constant_sampling['temp_calculated'][:20])
plt.show()

# Temperature Plotting

Noise is visible as soon as the temperature sensor is touched or connected to ground in an improper way.

In [ ]:
idx_count = len(temperature_measurement.index)
@interact(low=(0,idx_count -1,10), high=(0, idx_count-1, 10))
def plot_temp(low=0, high=idx_count-1):
    fig, ax = plt.subplots(nrows=3, ncols=1, figsize=(28,9*3), sharex=True)
    ax[0].plot(temperature_measurement['Time'][low:high], temperature_measurement['adc_results.pa2_raw'][low:high])
    ax[1].plot(temperature_measurement['Time'][low:high], temperature_measurement['ext_lf_corr'][low:high])
    ax[2].plot(temperature_measurement['Time'][low:high], temperature_measurement['temp_calculated'][low:high])
    titles = ['Raw ADC Results', 'Low Pass Filtered Resistance Reading', 'Calculated Low Frequency Temperature']
    for i, title in zip(range(0,3), titles):
        ax[i].grid()
        ax[i].set_title(title)
    plt.plot()

# Temperature Plotting With Proper Grounding of Circuit and the Cable Shield

In [ ]:
# Derivateve of temp
shielded_df['temp_gradient'] = shielded_df['temp_calculated'].diff() / shielded_df['Time'].diff()

# Low pass filter gradient with moving average
shielded_df['temp_gradient_lf'] = 0.0
shielded_df['temp_gradient_lf_2'] = 0.0
last_grad_lf = 0.0

alpha = 0.005
delta_alpha = 0.00
zeta = 20

for index, row in shielded_df.iterrows():
    if index == 0:
        pass
    else:
        current_gradient = row['temp_gradient']
        if last_grad_lf != 0.0:
            alpha_corr = abs(current_gradient) / zeta  * delta_alpha
        else:
            alpha_corr = 0
        last_grad_lf = last_grad_lf * (1-(alpha+alpha_corr)) + (alpha+alpha_corr) * current_gradient
        shielded_df.at[index, 'temp_gradient_lf'] = last_grad_lf
        
# Derivateve of grad is grad2
shielded_df['temp_gradient_lf_2'] = shielded_df['temp_gradient_lf'].diff() / shielded_df['Time'].diff()

## Full curve

In [ ]:
fig, ax = plt.subplots(figsize=(28,9))
tau = 25
tau2 = 0
ax.plot(shielded_df['Time'], shielded_df['temp_calculated'], label='Uncalibrated Temperature')
ax.plot(shielded_df['Time'], shielded_df['temp_calculated']+shielded_df['temp_gradient_lf']*tau + shielded_df['temp_gradient_lf_2']*tau2, label=r'PT1 corrected with $\tau = %f$' % tau)
ax.grid()
ax.legend()
ax.set_title('Temperature measurement with proper ground connection')
plt.show()

## Temperature Gradient Noise vs Moving Average
### Time Domain

In [ ]:
fig, ax = plt.subplots(figsize=(28,8))
tau = 30
ax.plot(shielded_df['Time'], shielded_df['temp_gradient'], label=r"$\dot{\vartheta} = \frac{\partial\vartheta}{\partial t}$")
ax.plot(shielded_df['Time'], shielded_df['temp_gradient_lf'], label=r'$\tilde{\dot{\vartheta}}$')
ax.legend()
plt.show()

## Cooldown to Room Temperature in Detail

In [ ]:
fig, ax = plt.subplots(figsize=(28,9))
start_time = -320
filtered_cooldown = shielded_df[shielded_df['Time'] > start_time]
ax.plot(filtered_cooldown['Time'], filtered_cooldown['temp_calculated'], label='Measured Cooldown')
ax.plot(filtered_cooldown['Time'], filtered_cooldown['temp_calculated']+filtered_cooldown['temp_gradient_lf']*tau, label='Calculated Exterior Temperature')
ax.grid()
ax.set_title('Cooldown without airflow | Convection has to be taken into account') 
plt.show()

---
# Target Implementation Sampling of 1k Resistor

## Histograms

In [ ]:
# Read in data
kilo_ohm_sampling1 = pd.read_csv(r'1000OhmSamplingFixedStableCircuit.csv')
kilo_ohm_sampling1_ht = pd.read_csv(r'1000OhmSamplingFixedStableCircuitHT.csv')
kilo_ohm_sampling2 = pd.read_csv(r'1000OhmSamplingFixedStableCircuitDay2.csv')
plot_data_tuples = [(kilo_ohm_sampling1, 'Day 1 Sampling -- Stable circuit -- RT'),
                    (kilo_ohm_sampling1_ht, 'Day 1 Sampling -- Stable circuit -- HT'),
                    (kilo_ohm_sampling2, 'Day 2 Sampling -- Stable circuit'),
                    (pd.read_csv(r'1000OhmSamplingFixedStableCircuitDay3.csv'), 'Day 3 Sampling -- Stable Circuit (improved)'),
                    (pd.read_csv(r'1000OhmSamplingFixedStableCircuitDay4.csv'), 'Day 4 Sampling -- Stable Circuit (improved)'),
                    (pd.read_csv(r'1000OhmSampling-v1.2.csv'), 'Day 1 Sampling v1.2')
                   ]


In [ ]:

# def plot_histogram(ax, data, bin_count, title, signal_name):
# def calculate_temp_for_df(data_frame, resistance_col_name='ext_lf_corr', temp_col_name='temp_calculated'):

fig, axes = plt.subplots(nrows=len(plot_data_tuples), ncols=2, sharex='col', figsize=(28, 8*len(plot_data_tuples)))

if len(plot_data_tuples) == 1:
    axes = [axes]

for df, title in plot_data_tuples:
    calculate_temp_for_df(df, resistance_col_name='pt1000_value')

for (df,title),ax in zip(plot_data_tuples, axes):
    plot_histogram(ax[0], df['pt1000_value'], 21, title, 'PT1000 Resistance')
    plot_histogram(ax[1], df['temp_calculated'], 21, title, 'Calculated Temperature in °C')
    ax[0].grid()
    ax[1].grid()

plt.tight_layout()
plt.show()

In [ ]:
fig, axes = plt.subplots(nrows=1, ncols=2, sharex='col', figsize=(28, 8))
v12_df = pd.read_csv(r'hw-v12-1000Ohm.csv')                       
plot_histogram(axes[0], v12_df['pt1000_res_raw_lf'], 21, 'HW v1.2 1k Ohm Sampling', '1k Resistance')
plot_histogram(axes[1], v12_df['adc_pt1000_raw_reading_hf'], 21, 'HW v1.2 1k Ohm Sampling', '1k Resistance')

In [ ]:
print(calc_temp(1000.6)-calc_temp(1000.4))

adc_min_res = 1/4095*2500
print('Min res: ', adc_min_res)

print(calc_temp(2000))
print(calc_temp(2000+adc_min_res))